### Illustrative Hedging Profit Calculations with Brownian Blancmange

© 2022 Oliver Bentley and Andrew D Smith. For educational purposes only. We accept no liability for any loss you may suffer etc.

Converted to Python / Jupyter Notebooks by Carl Dowthwaite 2022

License GPL 3.0

In [1]:
import math
from scipy.stats import norm

In [2]:
b_factors = {}
b_factors["1A"] = {"c1": [-0.5, 0.0, 0.0, 0.5], "m1": [0.5, -0.5, 0.5, 0.5], "c2": [1.0, 2.0, -2.0, -3.0], "m2": [-4.0, -4.0, 4.0, 4.0]}
b_factors["1B"] = {"c1": [0.0, 0.0, 0.0, 1.0], "m1": [-0.5, -0.5, 0.5, -0.5], "c2": [0.0, 2.0, -2.0, 4.0], "m2": [4.0, -4.0, 4.0, -4.0]}
b_factors["2A"] = {"c1": [0.5, 0.0, 0.0, 0.5], "m1": [-0.5, 0.5, 0.5, 0.5], "c2": [1.0, 2.0, -2.0, -3.0], "m2": [-4.0, -4.0, 4.0, 4.0]}
b_factors["2B"] = {"c1": [0.0, 0.0, 0.0, 1.0], "m1": [0.5, 0.5, 0.5, -0.5], "c2": [0.0, 2.0, -2.0, 4.0], "m2": [4.0, -4.0, 4.0, -4.0]}
b_factors["3A"] = {"c1": [0.0, 0.5, 0.5, 1.0], "m1": [0.5, 0.5, 0.5, -0.5], "c2": [0.0, -1.0, 3.0, 4.0], "m2": [4.0, 4.0, -4.0, -4.0]}
b_factors["3B"] = {"c1": [0.5, 0.5, 0.5, 0.5], "m1": [-0.5, 0.5, 0.5, 0.5], "c2": [1.0, -1.0, 3.0, -3.0], "m2": [-4.0, 4.0, -4.0, 4.0]}
b_factors["4A"] = {"c1": [0.0, 0.5, 1.5, 1.0], "m1": [0.5, 0.5, -0.5, 0.5], "c2": [0.0, -1.0, 3.0, 4.0], "m2": [4.0, 4.0, -4.0, -4.0]}
b_factors["4B"] = {"c1": [0.5, 0.5, 1.5, 1.5], "m1": [-0.5, 0.5, -0.5, -0.5], "c2": [1.0, -1.0, 3.0, -3.0], "m2": [-4.0, 4.0, -4.0, 4.0]}

In [3]:
def Blancmange(ID, t):
    b_factors_id = b_factors[ID]
    c1, c2, m1, m2 = b_factors_id["c1"], b_factors_id["c2"], b_factors_id["m1"], b_factors_id["m2"], 
    if t <= 0:
        B = 0
    elif t >= 1:
        B = 1
    elif t < 0.25:
        B = c1[0] + m1[0] * Blancmange(ID, c2[0] + m2[0] * t)
    elif t < 0.5:
        B = c1[1] + m1[1] * Blancmange(ID, c2[1] + m2[1] * t)
    elif t < 0.75:
        B = c1[2] + m1[2] * Blancmange(ID, c2[2] + m2[2] * t)
    else:
        B = c1[3] + m1[3] * Blancmange(ID, c2[3] + m2[3] * t)
    return B

In [4]:
def RealisedVol(ID, n):
    # Realised volatility. n should be positive.
    temp = 0
    thisf = 0
    for j in range(1,n+1):
        lastf = thisf
        thisf = Blancmange(ID, j / n)
        temp = temp + (thisf - lastf) ** 2
    return math.sqrt((n * temp - 1) / (n - 1))

In [5]:
def HedgeProfit(ID, S0, S1, Strike, OpTerm, RealisedVol, ImpliedVol, nsteps, IsNet):
    
    #Profit on operating a delta hedge, either on an asset only basis (IsNet = False) or net of BS option increase (IsNet = True)
    #ID must be one of 8 permitted ID's, S0 and S1 must be positive, OpTerm must be at least 1, ImpliedVol must be positive.
    #Interest and dividends assumed (without much loss of generality) to be zero.
    #This is based on call options, bit if IsNet then the puts would be exactly the same.

    CumProfit = 0
    Snext = S0
    t = 0

    for j in range(1, nsteps + 1):
        Slast = Snext
        Delta = norm.cdf(math.log(Slast / Strike) / ImpliedVol / math.sqrt(OpTerm - t) + 0.5 * ImpliedVol * math.sqrt(OpTerm - t))
        t = j / nsteps
        Snext = S0 ** (1 - t) * S1 ** t * math.exp(RealisedVol * (Blancmange(ID, t) - t))
        CumProfit = CumProfit + Delta * (Snext - Slast)

    if IsNet:
        #subtract increase in liability value
        #using Black-Scholes option pricing formula
        CumProfit = CumProfit + S0 * norm.cdf(math.log(S0 / Strike) / ImpliedVol / math.sqrt(OpTerm) + 0.5 * ImpliedVol * math.sqrt(OpTerm)) \
                        - Strike * norm.cdf(math.log(S0 / Strike) / ImpliedVol / math.sqrt(OpTerm) - 0.5 * ImpliedVol * math.sqrt(OpTerm))
                        
    if OpTerm == 1:
        #Option expires at interval end
        if S1 > Strike:
            CumProfit = CumProfit - S1 + Strike
    else:
        CumProfit = CumProfit - S1 * norm.cdf(math.log(S1 / Strike) / ImpliedVol / math.sqrt(OpTerm - 1) + 0.5 * ImpliedVol * math.sqrt(OpTerm - 1)) \
                        + Strike * norm.cdf(math.log(S1 / Strike) / ImpliedVol / math.sqrt(OpTerm - 1) - 0.5 * ImpliedVol * math.sqrt(OpTerm - 1))


    return CumProfit

In [6]:
initial_underlying = 120
final_underlying = 40
strike = 100
option_term = 2
realised_vol = 0.3
implied_vol = 0.2
no_of_steps = 256
include_liabs = True

In [7]:
start_final_underlying = 40
end_final_underlying = 200
step_final_underlying = 5
underlyings = list(range(start_final_underlying, end_final_underlying + step_final_underlying, step_final_underlying))

In [8]:
hedge_results = {"positive": {}, "negative": {}}
for realised_vol_sign in hedge_results.keys():
    for pattern in b_factors.keys():
        results = []
        for final_underlying in underlyings:
            if realised_vol_sign == "positive":
                rvs = + 1.0
            else:
                rvs = -1.0
            r = HedgeProfit(pattern, initial_underlying, final_underlying, strike, option_term, realised_vol * rvs, implied_vol, no_of_steps, include_liabs)
            results.append(r)
        hedge_results[realised_vol_sign][pattern] = results

In [9]:
%matplotlib widget
import numpy as np
import matplotlib.pyplot as plt

# Dataset
x = np.array(underlyings)

for realised_vol_sign in hedge_results.keys():
    for pattern in b_factors.keys():
        y = np.array(hedge_results[realised_vol_sign][pattern])
        # Plotting the Graph
        if hedge_results[realised_vol_sign][pattern][0] > -1.75:
            line_color = "blue"
        else:
            line_color = "red"
        plt.plot(x, y, color=line_color)
    
plt.xlabel("Year End Price of Underlying Asset")
plt.ylabel("Hedge Profit")
plt.grid(True)
plt.show()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [10]:
def gen_blancmange_results(ID, steps):
    x = np.array(list([x / steps for x in range(0, steps + 1)]))
    y = np.array(list([Blancmange(ID, x / steps) for x in range(0, steps + 1)]))
    return x, y  

In [11]:
plt.figure(2)

x, y = gen_blancmange_results("1A", 1024)
xd, yd = gen_blancmange_results("1A", 16)

plt.plot(x, y)
plt.plot(xd, yd, linestyle="None", marker = "o", color="red")
    
plt.xlabel("t")
plt.ylabel("Blancmange")
plt.grid(True)
plt.show()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [12]:
plt.figure(4)

xd, yd = gen_blancmange_results("1A", 64)
xd2, yd2 = gen_blancmange_results("1A", 16)

plt.plot(xd, yd, linestyle="None", marker = "o", color="red")
plt.plot(xd2, yd2, linestyle="None", marker = "o", color="blue")

    
plt.xlabel("t")
plt.ylabel("Blancmange")
plt.grid(True)
plt.show()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …